In [1]:
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix

In [56]:
def evaluate_rule_conditions(row, condition_part):

    # Checks if any of the conditions in the rule are satisfied
    if all(check_condition(row, part) for part in condition_part.split(" and ")):
        return True  # Return True if all conditions in the rule are satisfied
    
    return False  # Return False if any of the conditions in the rule is not satisfied


def check_condition(row, condition_part):
    # Check if a single condition part is satisfied
    
    #parts = [part.strip('()') for part in condition_part.split()]
    #parts = [part for part in condition_part.split()]
    # Use regular expressions to properly parse the condition
    parts = re.split(r'\s*(==|<=|>=|<|>|!=)\s*', condition_part)
    
    #print("parts: ", parts)
    if len(parts) == 3:
        column, op, value = parts
        return eval(f"{row[column]} {op} {value}")
    # handle the case of a 2-thresholds conditions of the kind: a < Column <= b
    elif len(parts) == 5:
        val1,op1,column,op2,val2 = parts
        # Use the original condition from the rule
        return eval(f"{val1} {op1} {row[column]} {op2} {val2}")        
    else:
        RaiseValueError("Bad condition formatting!")


def evaluate_rules(data, N1, tuned_rules, output, dataset_name = None):

    idx_rules = 0
    satisfiedMat = np.zeros((len(data),len(tuned_rules)))
    coveringlist = []
    errorlist = []
    precisionlist = []
    for i, rule in tuned_rules.iterrows():
        pred_rule = []
        tptot = 0
        tntot = 0
        fntot = 0
        fptot = 0
        
        idx_data = 0
        tuned_antecedent = rule['Rule'].strip()
        print(f"rule: {tuned_antecedent}")
        for j, row in data.iterrows():
            print(row)
            y_row = row[output]
            tp = 0
            tn = 0
            fn = 0
            fp = 0
            # check if the point row satifies rule 
            if evaluate_rule_conditions(row, tuned_antecedent):
                # rule is satisfied
                satisfied = True              
                satisfiedMat[idx_data,idx_rules] = 1
                print("satisfied")
            else:
                satisfied = False
                print("not satisfied")
    

            if satisfied and y_row == 1:
                tp=1
            elif satisfied and y_row == 0:
                fp=1
            elif not satisfied and y_row == 0:
                tn=1
            
            elif not satisfied and y_row == 1:
                fn=1

            tptot+=tp
            tntot+=tn
            fptot+=fp
            fntot+=fn
            idx_data+=1
        if (tptot+fptot) == 0 and (fptot+tntot)==0: 
            coveringlist.append(tptot/(tptot+fntot))
            errorlist.append(0)
            precisionlist.append(0)
            print(f"tp = {tptot}, fp = {fptot}, tn = {tntot}, fn = {fntot}")
            print(f"covering = {cov}, error = 0, precision = 0")
            #continue
        elif (tptot+fptot) == 0:
            err = fptot/(tntot+fptot)
            coveringlist.append(tptot/(tptot+fntot))
            print(f"tp = {tptot}, fp = {fptot}, tn = {tntot}, fn = {fntot}")
            print(f"covering = {cov}, error = {err}, precision = 0")
            errorlist.append(err)
            precisionlist.append(0)
            #continue
        elif (tntot+fptot)==0:
            errorlist.append(0)
            cov = tptot/(tptot+fntot)
            prec = tptot/(tptot+fptot)
            print(f"tp = {tptot}, fp = {fptot}, tn = {tntot}, fn = {fntot}")
            print(f"covering = {cov}, error = 0, precision = {prec}")
            coveringlist.append(cov)
            precisionlist.append(prec)
            #continue
        elif (tptot+fntot)==0:
            coveringlist.append(0)
            err = fptot/(tntot+fptot)
            prec = tptot/(tptot+fptot)
            print(f"tp = {tptot}, fp = {fptot}, tn = {tntot}, fn = {fntot}")
            print(f"covering = 0, error = {err}, precision = {prec}")
            errorlist.append(err)
            precisionlist.append(prec)
            #continue
        else:
            
            #cov = tptot/N1
            cov = tptot/(tptot+fntot)
            err = fptot/(tntot+fptot)
            prec = tptot/(tptot+fptot)
            print(f"tp = {tptot}, fp = {fptot}, tn = {tntot}, fn = {fntot}")
            print(f"covering = {cov}, error = {err}, precision = {prec}")
            coveringlist.append(cov)
            errorlist.append(err)
            precisionlist.append(prec)
            #continue
        idx_rules+=1
        print("\n")
    
    return satisfiedMat, coveringlist, precisionlist, errorlist




In [23]:
def ReformattingRuleset(rules, output_label):
    #print(output_label)
    # adjust columns values
    for i in range(len(rules)+1):   
        rules["Rule"] = rules["Rule"].apply(lambda x: x.replace("RULE {}: ".format(i),""))
    rules["Rule"] = rules["Rule"].apply(lambda x: x.replace("AND","and"))
    rules["Rule"] = rules["Rule"].apply(lambda x: x.replace("{",""))
    rules["Rule"] = rules["Rule"].apply(lambda x: x.replace("}",""))
    rules["Rule"] = rules["Rule"].apply(lambda x: x.replace(f"{output_label} in ",f"{output_label} = "))
    rules["Covering"] = rules["Covering"].apply(lambda x: x.replace("COVERING: ",""))
    rules["Error"] = rules["Error"].apply(lambda x: x.replace("ERROR: ",""))
    rules['Output'] = rules['Rule'].str.extract(rf'{output_label} = (\d+)', expand=False).astype(int)
    rules["Rule"] = rules["Rule"].apply(lambda x: x.replace("IF ",""))
    rules["Rule"] = rules["Rule"].apply(lambda x: x.replace(x[x.find("THEN"):],""))
    
    return rules

In [4]:
def calculate_metrics(data, output_label, reapply_on_gt = False, gt_label = None):
    #print(data[output_label])
    #print(data["pred("+ output_label+ ")"])
    if reapply_on_gt:
        cm = confusion_matrix(data[gt_label], data["pred("+ output_label+ ")"], labels=[0, 1])
    else:
        cm = confusion_matrix(data[output_label], data["pred("+ output_label+ ")"], labels=[0, 1])
    #print(cm)
    TN, FP, FN, TP = cm.ravel()
    FNR = FN / (FN + TP) if TP + FN != 0 else 0
    TNR = TN / (TN + FP) if TN + FP != 0 else 0
    FPR = FP / (FP + TN) if TN + FP != 0 else 0
    TPR = TP / (TP + FN) if TP + FN != 0 else 0
    Acc = (TP + TN) / (TP + TN + FP + FN)
    f1score = (2 * TP) / (2 * TP + FP + FN)
    PPV = TP / (TP + FP) if TP + FP != 0 else 0
    NPV = TN / (TN + FN) if TN + FN != 0 else 0
    return FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV

In [6]:
datasetlist = ['ssh', 'p2p', 'smoking', 'cardio', 'platooning', 'rul', 'eeg', 'mqttset', 'telescope', 'fire']
outputlabels = ['g', 'g', 'smoking', 'cardio', 'collision', 'RUL_binary', 'eyeDetection', 'output', 'class', 'Fire Alarm']

# Performance of the LLM 

**1 ) Original test data;**

**2) New rules trained on CCS points, with original output labels**

**3) New rules trained with respect to belonging or not to CCS**


In [ ]:

data = []

for dataset_name, output_label in zip(datasetlist, outputlabels):
    dataORIG = pd.read_excel(f"results_rev_paper_20240325/results_eps005_{dataset_name}.xlsx")
    FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV = calculate_metrics(dataORIG, output_label)
    data.append([dataset_name, 'Original', FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV])

    dataCCS = pd.read_excel(f"results_rev_paper_20240325/prove_ccs/{dataset_name}_ccs_testset.xlsx")
    FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV = calculate_metrics(dataCCS, output_label)
    data.append([dataset_name, 'New rules on ccs for original output', FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV])

    dataCCS2 = pd.read_excel(f"results_rev_paper_20240325/prove_ccs/{dataset_name}_testset.xlsx")
    FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV = calculate_metrics(dataCCS2, "ConformalPoint")
    data.append([dataset_name, 'New rules for ccs output', FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV])

df = pd.DataFrame(data, columns=['Dataset', 'Rules', 'FNR', 'TNR', 'TPR', 'FPR', 'Accuracy', 'F1 Score', 'Precision', 'NPV'])

# Save DataFrame to an Excel file
#df.to_excel("metrics_table.xlsx", index=False)

In [15]:
df.to_excel("results_rev_paper_20240325/prove_ccs/metrics_LLM_CCS.xlsx", index=False)

**Original rules vs rules predicting ccs/non ccs evaluated on ccs/non ccs labels or ground truth** 

In [17]:
data = []

for dataset_name, output_label in zip(datasetlist, outputlabels):
    dataORIG = pd.read_excel(f"results_rev_paper_20240325/results_eps005_{dataset_name}.xlsx")
    FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV = calculate_metrics(dataORIG, output_label)
    data.append([dataset_name, 'Original', FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV])

    dataCCS2 = pd.read_excel(f"results_rev_paper_20240325/prove_ccs/{dataset_name}_testset.xlsx")
    FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV = calculate_metrics(dataCCS2, "ConformalPoint")
    data.append([dataset_name, 'New rules for ccs output', FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV])

    dataCCS3 = pd.read_excel(f"results_rev_paper_20240325/prove_ccs/{dataset_name}_testset.xlsx")
    FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV = calculate_metrics(dataCCS3, "ConformalPoint", reapply_on_gt = True, gt_label = output_label)
    data.append([dataset_name, 'New rules for ccs output - test on original output', FNR, TNR, TPR, FPR, Acc, f1score, PPV, NPV])

df2 = pd.DataFrame(data, columns=['Dataset', 'Rules', 'FNR', 'TNR', 'TPR', 'FPR', 'Accuracy', 'F1 Score', 'Precision', 'NPV'])
df2

Dataset                                              Rules       FNR  \
0          ssh                                           Original  0.180249   
1          ssh                           New rules for ccs output  0.151596   
2          ssh  New rules for ccs output - test on original ou...  0.358268   
3          p2p                                           Original  0.000000   
4          p2p                           New rules for ccs output  0.000000   
5          p2p  New rules for ccs output - test on original ou...  0.000000   
6      smoking                                           Original  0.187746   
7      smoking                           New rules for ccs output  0.152000   
8      smoking  New rules for ccs output - test on original ou...  0.445087   
9       cardio                                           Original  0.307516   
10      cardio                           New rules for ccs output  0.112676   
11      cardio  New rules for ccs output - test on original ou...  0.534840   
12  platooning                                           Original  0.121041   
13  platooning                           New rules for ccs output  0.023810   
14  platooning  New rules for ccs output - test on original ou...  0.284211   
15         rul                                           Original  0.245059   
16         rul                           New rules for ccs output  0.303030   
17         rul  New rules for ccs output - test on original ou...  0.468085   
18         eeg                                           Original  0.227273   
19         eeg                           New rules for ccs output  0.428571   
20         eeg  New rules for ccs output - test on original ou...  0.560000   
21     mqttset                                           Original  0.104194   
22     mqttset                           New rules for ccs output  0.000000   
23     mqttset  New rules for ccs output - test on original ou...  0.113636   
24   telescope                                           Original  0.228814   
25   telescope                           New rules for ccs output  0.128205   
26   telescope  New rules for ccs output - test on original ou...  0.371429   
27        fire                                           Original  0.022063   
28        fire                           New rules for ccs output  0.065831   
29        fire  New rules for ccs output - test on original ou...  0.118343   

         TNR       TPR       FPR  Accuracy  F1 Score  Precision       NPV  
0   0.941411  0.819751  0.058589  0.880800  0.872650   0.932846  0.840270  
1   0.953526  0.848404  0.046474  0.914000  0.881215   0.916667  0.912577  
2   0.955285  0.641732  0.044715  0.796000  0.761682   0.936782  0.720859  
3   0.972898  1.000000  0.027102  0.986400  0.986535   0.973427  1.000000  
4   0.953878  1.000000  0.046122  0.978000  0.979401   0.959633  1.000000  
5   0.924797  1.000000  0.075203  0.963000  0.964862   0.932110  1.000000  
6   0.650419  0.812254  0.349581  0.708000  0.664368   0.562038  0.862495  
7   0.766857  0.848000  0.233143  0.777000  0.487356   0.341935  0.972464  
8   0.819572  0.554913  0.180428  0.728000  0.585366   0.619355  0.776812  
9   0.754519  0.692484  0.245481  0.722000  0.723108   0.756565  0.690119  
10  0.785548  0.887324  0.214452  0.800000  0.557522   0.406452  0.976812  
11  0.865672  0.465160  0.134328  0.653000  0.587396   0.796774  0.588406  
12  0.861111  0.878959  0.138889  0.869000  0.855727   0.833691  0.899813  
13  0.868613  0.976190  0.131387  0.902500  0.863158   0.773585  0.987552  
14  0.890476  0.715789  0.109524  0.807500  0.779370   0.855346  0.775934  
15  0.802491  0.754941  0.197509  0.787730  0.688288   0.632450  0.879142  
16  0.900000  0.696970  0.100000  0.858896  0.666667   0.638889  0.921260  
17  0.905172  0.531915  0.094828  0.797546  0.602410   0.694444  0.826772  
18  0.785894  0.772727  0.214106  0.779706  0.767278   0.761905  0.795918  
19  0.824074  0.571429  0.175926  0.7

In [19]:
df2.to_excel("results_rev_paper_20240325/prove_ccs/metrics_LLM_CCS_v2.xlsx", index=False)

## Rule-by-rule performance for rules predicting the $\in \mathcal{S}_\varepsilon$ class

**1) Conformal Output**

In [ ]:
rulevalid = []
dataset_name = "ssh"
output_label = "g"
#for dataset_name, output_label in zip(datasetlist, outputlabels):
print(f"DATASET: {dataset_name.upper()}")
data = pd.read_excel(f"results_rev_paper_20240325/prove_ccs/{dataset_name}_testset.xlsx")

rules = pd.read_csv(f"results_rev_paper_20240325/prove_ccs/ruleset_ccs/{dataset_name}_ccs_approx_rules.csv", header=None, names=["Rule", "Covering", "Error"])
rules = ReformattingRuleset(rules, "ConformalPoint")

N1 = len(data[data[output_label] == 1])

rules_targetcls = rules[rules["Output"]==1]

_, coveringvaluesCCS,precisionCCS,errorCCS = evaluate_rules(data, N1, rules_targetcls, "ConformalPoint",dataset_name = dataset_name)
_, coveringvaluesCCS2,precisionCCS2,errorCCS2 = evaluate_rules(data, N1, rules_targetcls, output_label,dataset_name = dataset_name)
    
df = pd.DataFrame(data = zip([dataset_name]*len(rules_targetcls),list(rules_targetcls["Rule"]),coveringvaluesCCS,coveringvaluesCCS2,precisionCCS,precisionCCS2,errorCCS,errorCCS2), columns = ["Dataset","Rule","CoveringCCS","CoveringGT","PrecisionCCS","PrecisionGT","ErrorCCS","ErrorGT"])
rulevalid.append(df)

mA                      -1.128277
mQ                       2.654966
mDt                      0.196057
vA                      -1.023756
vQ                       3.374217
vDt                     -0.115699
sA                       1.241052
sQ                       1.102082
sDt                     -0.785768
kA                       1.525656
kQ                      -0.083620
kDt                     -0.488013
g                        0.000000
ConformalPoint           0.000000
pred(ConformalPoint)     0.000000
conf(ConformalPoint)     0.072313
rule(ConformalPoint)     5.000000
nrule(ConformalPoint)    1.000000
err(ConformalPoint)      0.000000
rule-1                   5.000000
out-1                    0.000000
conf-1                   0.072313
rule-2                        NaN
out-2                         NaN
conf-2                        NaN
rule-3                        NaN
out-3                         NaN
conf-3                        NaN
rule-4                        NaN
out-4         

mA                       0.993238
mQ                      -0.061212
mDt                      0.072245
vA                       1.991709
vQ                      -0.422519
vDt                     -0.115820
sA                      -0.513426
sQ                      -0.566490
sDt                     -0.649468
kA                      -0.653021
kQ                      -0.083620
kDt                     -0.442791
g                        0.000000
ConformalPoint           0.000000
pred(ConformalPoint)     0.000000
conf(ConformalPoint)     0.292197
rule(ConformalPoint)     1.000000
nrule(ConformalPoint)    2.000000
err(ConformalPoint)      0.000000
rule-1                   1.000000
out-1                    0.000000
conf-1                   0.232592
rule-2                   6.000000
out-2                    0.000000
conf-2                   0.059605
rule-3                        NaN
out-3                         NaN
conf-3                        NaN
rule-4                        NaN
out-4         

mA                        0.931176
mQ                        2.387281
mDt                       0.265229
vA                        1.108549
vQ                       -0.366184
vDt                      -0.115434
sA                       -1.000860
sQ                       -0.323633
sDt                      -0.825461
kA                       -1.074983
kQ                       -0.083620
kDt                      -0.501638
g                         1.000000
ConformalPoint            0.000000
pred(ConformalPoint)      1.000000
conf(ConformalPoint)      0.747275
rule(ConformalPoint)      9.000000
nrule(ConformalPoint)     4.000000
err(ConformalPoint)       1.000000
rule-1                    9.000000
out-1                     1.000000
conf-1                    0.397849
rule-2                   10.000000
out-2                     1.000000
conf-2                    0.339758
rule-3                    6.000000
out-3                     0.000000
conf-3                    0.059605
rule-4              

mA                       -0.986416
mQ                        0.110056
mDt                       0.365674
vA                       -0.864481
vQ                       -0.408873
vDt                      -0.115191
sA                       -1.150356
sQ                       -0.526184
sDt                      -0.852809
kA                       -0.995119
kQ                       -0.083620
kDt                      -0.511678
g                         1.000000
ConformalPoint            1.000000
pred(ConformalPoint)      1.000000
conf(ConformalPoint)      0.737606
rule(ConformalPoint)      9.000000
nrule(ConformalPoint)     2.000000
err(ConformalPoint)       0.000000
rule-1                    9.000000
out-1                     1.000000
conf-1                    0.397849
rule-2                   10.000000
out-2                     1.000000
conf-2                    0.339758
rule-3                         NaN
out-3                          NaN
conf-3                         NaN
rule-4              

mA                       0.714833
mQ                       1.648293
mDt                     -0.301489
vA                       2.012587
vQ                       3.380818
vDt                     -0.116715
sA                       0.961332
sQ                       1.103342
sDt                      0.048909
kA                       0.999824
kQ                      -0.083620
kDt                     -0.136812
g                        0.000000
ConformalPoint           0.000000
pred(ConformalPoint)     0.000000
conf(ConformalPoint)     0.362162
rule(ConformalPoint)     2.000000
nrule(ConformalPoint)    3.000000
err(ConformalPoint)      0.000000
rule-1                   2.000000
out-1                    0.000000
conf-1                   0.230244
rule-2                   5.000000
out-2                    0.000000
conf-2                   0.072313
rule-3                   6.000000
out-3                    0.000000
conf-3                   0.059605
rule-4                        NaN
out-4         

...

mA                        0.724008
mQ                        1.097699
mDt                      -0.128239
vA                        0.506083
vQ                       -0.407098
vDt                      -0.116360
sA                       -1.138434
sQ                       -0.523973
sDt                      -0.402243
kA                       -1.114241
kQ                       -0.083620
kDt                      -0.348949
g                         1.000000
ConformalPoint            1.000000
pred(ConformalPoint)      1.000000
conf(ConformalPoint)      0.737606
rule(ConformalPoint)      9.000000
nrule(ConformalPoint)     2.000000
err(ConformalPoint)       0.000000
rule-1                    9.000000
out-1                     1.000000
conf-1                    0.397849
rule-2                   10.000000
out-2                     1.000000
conf-2                    0.339758
rule-3                         NaN
out-3                          NaN
conf-3                         NaN
rule-4              

mA                        2.280525
mQ                        0.028228
mDt                      -0.052396
vA                        2.382781
vQ                       -0.415323
vDt                      -0.116249
sA                        0.062036
sQ                       -0.478211
sDt                      -0.559398
kA                        0.555420
kQ                       -0.083620
kDt                      -0.413887
g                         1.000000
ConformalPoint            1.000000
pred(ConformalPoint)      0.000000
conf(ConformalPoint)      0.159207
rule(ConformalPoint)      3.000000
nrule(ConformalPoint)     2.000000
err(ConformalPoint)       1.000000
rule-1                    3.000000
out-1                     0.000000
conf-1                    0.189402
rule-2                   13.000000
out-2                     1.000000
conf-2                    0.030194
rule-3                         NaN
out-3                          NaN
conf-3                         NaN
rule-4              

mA                      -0.729467
mQ                      -0.451956
mDt                     -0.215428
vA                      -0.571912
vQ                      -0.400328
vDt                     -0.116442
sA                       0.148604
sQ                      -0.531189
sDt                     -0.130848
kA                      -0.129601
kQ                      -0.083620
kDt                     -0.211578
g                        0.000000
ConformalPoint           0.000000
pred(ConformalPoint)     0.000000
conf(ConformalPoint)     0.652239
rule(ConformalPoint)     1.000000
nrule(ConformalPoint)    3.000000
err(ConformalPoint)      0.000000
rule-1                   1.000000
out-1                    0.000000
conf-1                   0.232592
rule-2                   2.000000
out-2                    0.000000
conf-2                   0.230244
rule-3                   3.000000
out-3                    0.000000
conf-3                   0.189402
rule-4                        NaN
out-4         

mA                       0.189406
mQ                      -1.229003
mDt                     -0.320336
vA                      -0.330705
vQ                      -0.412105
vDt                     -0.116700
sA                      -0.342787
sQ                      -0.556335
sDt                      0.288882
kA                      -0.249622
kQ                      -0.083620
kDt                      0.041010
g                        1.000000
ConformalPoint           0.000000
pred(ConformalPoint)     0.000000
conf(ConformalPoint)     0.462837
rule(ConformalPoint)     1.000000
nrule(ConformalPoint)    2.000000
err(ConformalPoint)      0.000000
rule-1                   1.000000
out-1                    0.000000
conf-1                   0.232592
rule-2                   2.000000
out-2                    0.000000
conf-2                   0.230244
rule-3                        NaN
out-3                         NaN
conf-3                        NaN
rule-4                        NaN
out-4         

KeyboardInterrupt: 

In [27]:
ValDf = pd.concat(rulevalid, ignore_index = True)
ValDf

Dataset                                               Rule  \
0          ssh                                   sA <= -0.770336    
1          ssh                sA <= -0.467081 and sQ > -0.528809    
2          ssh  -1.852861 < mQ <= 0.169999 and vA <= 0.536997 ...   
3          ssh                        -0.433821 < sQ <= 0.880432    
4          ssh      mA > 0.732053 and -0.086947 < kA <= 1.001915    
5          p2p                        -0.451570 < sQ <= 1.888989    
6          p2p                                    mQ > -0.385606    
7      smoking  age <= 1.103201 and height(cm) > -0.233761 and...   
8      smoking  -1.796235 < age <= 1.103201 and height(cm) > 0...   
9      smoking  -0.967826 < age <= 1.103201 and height(cm) > -...   
10     smoking  age <= 1.103201 and height(cm) > -0.233761 and...   
11     smoking  -0.967826 < age <= 1.103201 and triglyceride <...   
12     smoking  relaxation <= 0.567731 and triglyceride > 0.90...   
13     smoking  -1.796235 < age <= 1.517406 and -0.777564 < he...   
14     smoking  -1.796235 < age <= 1.517406 and height(cm) > -...   
15      cardio  weight <= 1.434065 and ap_hi > 0.114816 and ap...   
16      cardio  age <= 1.504776 and height > -1.444474 and wei...   
17      cardio  weight > 0.923495 and 0.066117 < ap_hi <= 0.42...   
18      cardio  0.267358 < age <= 1.238283 and height <= -0.10...   
19      cardio                                    age > 1.525447    
20      cardio  -1.369900 < age <= 1.527878 and -1.931681 < he...   
21      cardio  age > -0.382155 and height <= 0.747956 and wei...   
22      cardio  ap_hi > 0.101829 and 0.477999 < gluc <= 2.225438    
23  platooning                 PER > 0.838081 and v0 > -0.829500    
24  platooning  N > 0.880045 and PER > -0.966916 and v0 > -1.3...   
25  platooning  -0.870026 < N <= 0.880045 and F0 <= 1.065423 a...   
26  platooning                                    PER > 1.358754    
27  platooning                   N > 1.317562 and d0 <= 0.903621    
28         rul         v_Nc > -0.332015 and m_htBleed > 1.011872    
29         rul  v_Nc > -0.098953 and -0.236282 < m_htBleed <= ...   
30         rul  m_Nc > -0.977750 and v_Nc <= 0.512992 and 0.36...   
31         rul  -0.207890 < m_Nc <= 0.344699 and v_phi > 0.061...   
32         eeg  O1 <= -0.012571 and O2 > -1.047122 and T8 > -0...   
33         eeg    -0.000050 < AF3 <= 0.032671 and F7 <= 0.663631    
34         eeg     O1 > -0.001870 and -0.209757 < T8 <= 2.236390    
35         eeg  -0.899054 < F7 <= 0.540863 and P7 <= -0.009178...   
36         eeg  -0.017336 < AF3 <= -0.004989 and F7 <= -0.2963...   
37         eeg  F7 > -0.117711 and F3 > 0.007598 and FC5 > -0....   
38         eeg                       -0.016751 < O1 <= -0.015246    
39     mqttset                            mqtt.msgid > -0.605486    
40     mqttset                       tcp.time_delta <= -0.095065    
41     mqttset  -0.095059 < tcp.time_delta <= -0.081680 and mq...   
42   telescope  fSize > -0.641294 and 0.427665 < fAlpha <= 2.3...   
43   telescope         fLength > 0.466009 and fAlpha > -0.786871    
44   telescope  fWidth > -0.502929 and 0.271284 < fAlpha <= 1....   
45   telescope  fWidth <= -0.552714 and fSize > -0.774815 and ...   
46        fire                                   CNT > -0.330545    
47        fire    Raw H2 > 0.857229 and Pressure[hPa] > 0.878782    

    CoveringCCS  CoveringGT  PrecisionCCS  PrecisionGT  ErrorCCS   ErrorGT  
0      0.702128    0.525591      0.939502     0.950178  0.027244  0.028455  
1      0.587766    0.448819      0.917012     0.946058  0.032051  0.026423  
2      0.297872    0.246063      0.751678     0.838926  0.059295  0.048780  
3      0.114362    0.157480      0.524390     0.975610  0.062500  0.004065  
4      0.071809    0.064961      0.613636     0.750000  0.027244  0.022358  
5      0.996176    0.996063      0.983019     0.954717  0.018868  0.048780  
6      0.952199    0.950787      0.972656     0.943359  0.029350  0.058943  
7      0.

In [30]:
ValDf.to_excel("results_rev_paper_20240325/prove_ccs/ruleset_ccs/RuleByRuleValidCCS.xlsx", index = False)

## Evaluate the original rules on the (new) test sets

In [ ]:
rulevalid = []
#dataset_name = "ssh"
#output_label = "g"
for dataset_name, output_label in zip(datasetlist, outputlabels):
    print(f"DATASET: {dataset_name.upper()}")
    data = pd.read_excel(f"results_rev_paper_20240325/prove_ccs/{dataset_name}_testset.xlsx")
    
    rules = pd.read_csv(f"results_rev_paper_20240325/prove_ccs/ruleset_ccs/{dataset_name}_ccs_approx_rules.csv", header=None, names=["Rule", "Covering", "Error"])
    rules = ReformattingRuleset(rules, "ConformalPoint")
    
    N1 = len(data[data[output_label] == 1])
    
    rules_targetcls = rules[rules["Output"]==1]
    
    _, coveringvaluesCCS,precisionCCS,errorCCS = evaluate_rules(data, N1, rules_targetcls, "ConformalPoint",dataset_name = dataset_name)
    _, coveringvaluesCCS2,precisionCCS2,errorCCS2 = evaluate_rules(data, N1, rules_targetcls, output_label,dataset_name = dataset_name)
        
    df = pd.DataFrame(data = zip([dataset_name]*len(rules_targetcls),list(rules_targetcls["Rule"]),coveringvaluesCCS,coveringvaluesCCS2,precisionCCS,precisionCCS2,errorCCS,errorCCS2), columns = ["Dataset","Rule","CoveringCCS","CoveringGT","PrecisionCCS","PrecisionGT","ErrorCCS","ErrorGT"])
    rulevalid.append(df)